In [10]:
from scipy.io import wavfile

# sampling frequency, audio data
fs, audio_in = wavfile.read("./media/birds.wav")

In [11]:
import numpy as np
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

import plotly.graph_objs as go
import plotly.offline as py
from scipy.signal import spectrogram, decimate

def plot_spectrogram(samples, fs, decimation_factor=3, max_heat=50, mode='2D'):

    # optional decimate (downsample) audio
    if decimation_factor>1:
        samples_dec = decimate(samples, decimation_factor, zero_phase=True)
        fs_dec = int(fs / decimation_factor)
    else:
        samples_dec = samples
        fs_dec = fs
    
    # calculate spectrogram (array of FFTs from small windows of the signal)
    f_label, t_label, spec_data = spectrogram(
        samples_dec, fs=fs_dec, mode="magnitude"
    )

    # plotly heatmap/surface graph
    layout = go.Layout(
        height=500,
        # 2D axis titles
        xaxis=dict(title='Time (s)'),
        yaxis=dict(title='Frequency (Hz)'),
        # 3D axis titles
        scene=dict(
            xaxis=dict(title='Time (s)'),
            yaxis=dict(title='Frequency (Hz)'),
            zaxis=dict(title='Amplitude')
        )
    )

    trace = go.Heatmap(
        z=np.clip(spec_data,0,max_heat),
        y=f_label,
        x=t_label
    ) if mode=='2D' else go.Surface(
        z=spec_data,
        y=f_label,
        x=t_label
    )

    py.iplot(dict(data=[trace], layout=layout))

plot_spectrogram(audio_in, fs, mode='2D')



In [12]:
from scipy.signal import freqz, firwin

nyq = fs / 2.0 # nyquist frequency
taps = 99

# design high pass filter with cutoff at 2.8 kHz
hpf_coeffs = firwin(taps, 2800/nyq, pass_zero=False)

from scipy.signal import lfilter
import time

start_time = time.time()
# filter the audio
audio_hpf = lfilter(hpf_coeffs, 1.0, audio_in)
end_time = time.time()
print("Time cost with Python: {}s".format(end_time - start_time))

plot_spectrogram(audio_hpf, fs, mode='2D', max_heat=np.max(abs(audio_hpf)))

Time cost with Python: 0.023144006729125977s
